# Downloads, installs & imports

SPEGQL Schemas and datasets download and unzip


In [1]:
%%capture
!gdown https://drive.google.com/uc?id=1H026ff-czIdLH3saJzbWUH8VKOW3j63X
!unzip SPEGQL-dataset.zip

Spider datasets download

In [2]:
%%capture
!gdown https://drive.google.com/uc?id=14x6lsWqlu6gR-aYxa6cemslDN3qT3zxP
!unzip cosql_dataset.zip

In [3]:
%%capture
!gdown https://drive.google.com/uc?id=11icoH_EA-NYb0OrPTdehRWm_d7-DIzWX
!unzip spider.zip

Installs

In [4]:
%%capture
!pip install --upgrade jsonschema
!pip3 install git+https://github.com/acarrera94/text-to-graphql-validation --log ./logs.txt

In [5]:
!git clone https://github.com/huggingface/transformers
!pip install transformers==4.15.0


import transformers
print("my version of transformers is " + transformers.__version__)

# !pip install git+git://github.com/williamFalcon/pytorch-lightning.git@master --upgrade
# !pip install pytorch-lightning==0.6
!pip install torch==1.10.0
!pip install pytorch-lightning

fatal: destination path 'transformers' already exists and is not an empty directory.
my version of transformers is 4.15.0


In [6]:
import numpy as np
import pandas as pd

# # from tqdm import tqdm
import torch
from torch.utils.data import DataLoader, Dataset, RandomSampler, SequentialSampler, ConcatDataset
from torch.utils.data.sampler import SubsetRandomSampler
from torch.optim import Adam
import torch.nn.functional as F
from torch.utils.data import Dataset

from transformers import get_linear_schedule_with_warmup, AutoConfig 
from transformers import BartTokenizer,BartModel,BartForConditionalGeneration
from transformers import T5Tokenizer, T5ForConditionalGeneration, T5Model
from transformers import BartConfig
from transformers import AutoTokenizer
from transformers import AdamW
from torch.autograd import Variable

import pytorch_lightning as pl
from pytorch_lightning import Trainer


import os
from os.path import basename
import re
from functools import reduce

# #from graphqlval import exact_match
import itertools

torch.manual_seed(0)

import json
from pathlib import Path
from os.path import basename
import glob
from functools import reduce



# OPTIONAL: if you want to have more information on what's happening under the hood, activate the logger as follows
# import logging
# logging.basicConfig(level=logging.INFO)


/Users/jakobtolstrup/opt/anaconda3/lib/python3.9/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: dlopen(/Users/jakobtolstrup/opt/anaconda3/lib/python3.9/site-packages/torchvision/image.so, 6): Symbol not found: __ZN2at4_ops19empty_memory_format4callEN3c108ArrayRefINS2_6SymIntEEENS2_8optionalINS2_10ScalarTypeEEENS6_INS2_6LayoutEEENS6_INS2_6DeviceEEENS6_IbEENS6_INS2_12MemoryFormatEEE
  Referenced from: /Users/jakobtolstrup/opt/anaconda3/lib/python3.9/site-packages/torchvision/image.so
  Expected in: /Users/jakobtolstrup/opt/anaconda3/lib/python3.9/site-packages/torch/lib/libtorch_cpu.dylib
 in /Users/jakobtolstrup/opt/anaconda3/lib/python3.9/site-packages/torchvision/image.so
  warn(f"Failed to load image Python extension: {e}")


In [7]:
print("my version of pl is " + pl.__version__)

import transformers
print("my version of transformers is " + transformers.__version__)
print ("my version of pytorch is " + torch.__version__)

my version of pl is 1.9.3
my version of transformers is 4.15.0
my version of pytorch is 1.10.0


# Prepare GraphQL Dataset

In [8]:

class TextToGraphQLDataset(Dataset):
  'Characterizes a dataset for PyTorch'
  def __init__(self, tokenizer, type_path='train.json', block_size=102):
        'Initialization'
        super(TextToGraphQLDataset, ).__init__()
        self.tokenizer = tokenizer

        self.source = []
        self.target = []
        self.schema_ids = []
        root_path = './SPEGQL-dataset/'
        dataset_path = root_path + 'dataset/' + type_path

        schemas_path = root_path + 'Schemas/'
        schemas = glob.glob(schemas_path + '**/' + 'simpleSchema.json')

        self.max_len = 0
        self.name_to_schema = {}
        for schema_path in schemas:
           with open(schema_path, 'r') as s:
             data = json.load(s)

             type_field_tokens = [ ['<t>'] + [t['name']] + ['{'] + [ f['name'] for f in t['fields']] + ['}'] + ['</t>'] for t in data['types']]
             type_field_flat_tokens = reduce(list.__add__, type_field_tokens)

             arguments = [a['name']  for a in data['arguments']]
             schema_tokens = type_field_flat_tokens + ['<a>'] + arguments + ['</a>']

             path = Path(schema_path)
             schema_name = basename(str(path.parent))

             self.name_to_schema[schema_name] = schema_tokens

        with open(dataset_path, 'r') as f:
          data = json.load(f)

          for element in data:
            question_with_schema = 'translate English to GraphQL: ' + element['question']  + ' ' + ' '.join(self.name_to_schema[element['schemaId']]) + ' </s>'
            tokenized_s = tokenizer.encode_plus(question_with_schema,max_length=1024, pad_to_max_length=True, truncation=True, return_tensors='pt')
            self.source.append(tokenized_s)

            tokenized_t = tokenizer.encode_plus(element['query'] + ' </s>',max_length=block_size, pad_to_max_length=True, truncation=True, return_tensors='pt')
            self.target.append(tokenized_t)
            self.schema_ids.append(element['schemaId'])

  def get_question_with_schema(self, question, schemaId):
        return 'translate English to GraphQL: ' + question  + ' ' + ' '.join(self.name_to_schema[schemaId]) + ' </s>'


  def __len__(self):
        'Denotes the total number of samples'
        return len(self.source)

  def __getitem__(self, index):
        'Generates one sample of data'
        source_ids = self.source[index]['input_ids'].squeeze()
        target_ids = self.target[index]['input_ids'].squeeze()
        src_mask = self.source[index]['attention_mask'].squeeze()

        return { 
            'source_ids': source_ids,
                'source_mask': src_mask,
                'target_ids': target_ids,
                'target_ids_y': target_ids
                }

In [9]:
# tokenizer = AutoTokenizer.from_pretrained("t5-base")
# dataset = TextToGraphQLDataset(tokenizer=tokenizer, type_path='train.json', block_size=102)

# length = dataset.__len__()
# item = dataset.__getitem__(0)

So far:
- the max length of a tokenized question is **49**
- the max length of a tokenized query is **102**



In [10]:
class MaskGraphQLDataset(Dataset):
  'Characterizes a dataset for PyTorch'
  def __init__(self, tokenizer, type_path='train.json', block_size=64):
        'Initialization'
        super(MaskGraphQLDataset, ).__init__()
        self.tokenizer = tokenizer

        self.source = []
        self.target = []
        path = './SPEGQL-dataset/dataset/' + type_path
        with open(path, 'r') as f:
          data = json.load(f)
          for example in data:

            utterance = example['query']
            encoded_source = tokenizer.encode(utterance + ' </s>', max_length=block_size, padding='max_length', truncation=True, return_tensors='pt').squeeze()
            token_count = encoded_source.shape[0]
            repeated_utterance = [encoded_source for _ in range(token_count)]
            for pos in range(1, token_count):
              encoded_source = repeated_utterance[pos].clone()
              target_id = encoded_source[pos].item()
              if target_id == tokenizer.eos_token_id:
                  break
              encoded_source[pos] = tokenizer.mask_token_id
              decoded_target = ''.join(tokenizer.convert_ids_to_tokens([target_id])) + ' </s>'
              encoded_target = tokenizer.encode(decoded_target, return_tensors='pt', max_length=4, pad_to_max_length=True, truncation=True).squeeze()
              if encoded_target is not None and torch.numel(encoded_target) > 0:
                  self.target.append(encoded_target)
                  self.source.append(encoded_source)
              if torch.numel(encoded_target) > 0:
                  self.target.append(encoded_target)
                  self.source.append(encoded_source)


  def __len__(self):
        'Denotes the total number of samples'
        return len(self.source)

  def __getitem__(self, index):
        'Generates one sample of data'
        source_ids = self.source[index]
        target_id = self.target[index]
        return { 'source_ids': source_ids,
                'target_id': target_id}

In [11]:
# tokenizer = AutoTokenizer.from_pretrained("t5-base")

# special_tokens_dict = tokenizer.special_tokens_map # the issue could be here, might need to copy.
# special_tokens_dict['mask_token'] = '<mask>'
# special_tokens_dict['additional_special_tokens'] = ['<t>', '</t>', '<a>', '</a>']
# tokenizer.add_tokens(['{', '}', '<c>', '</c>'])
# tokenizer.add_special_tokens(special_tokens_dict)
# #model.resize_token_embeddings(len(tokenizer))
# print(tokenizer.mask_token)

# dataset = MaskGraphQLDataset(tokenizer=tokenizer, type_path='train.json', block_size=64)
# print(dataset)




# Prepare Spider Dataset

In [12]:
class SpiderDataset(Dataset):
  'Characterizes a dataset for PyTorch'
  def __init__(self, tokenizer, type_path='train_spider.json', block_size=102):
        'Initialization'
        super(SpiderDataset, ).__init__()
        self.tokenizer = tokenizer

        self.source = []
        self.target = []
        spider_path = './spider/'
        path = spider_path + type_path
        # TODO open up tables.json
        # its a list of tables
        # group by db_id 
        # grab column name from column_names_original ( each column name is a list of two. and the 2nd index {1} is the column name )
        # grab table names from table_names (^ same as above )
        # concat both with the english question (table names + <c> + column names + <q> english question)
        # tokenize

        # Maybe try making making more structure 
        # in the concat by using primary_keys and foreign_keys 

        tables_path = spider_path + 'tables.json'

        with open(path, 'r') as f, open(tables_path, 'r') as t:
          databases = json.load(t)
          data = json.load(f)

          #groupby db_id 
          grouped_dbs = {}
          for db in databases:
            grouped_dbs[db['db_id']] = db
          # print(grouped_dbs)
          # end grop tables

          for element in data:
            db = grouped_dbs[element['db_id']]

            # tables_names = " ".join(db['table_names_original'])
            db_tables = db['table_names_original']

            # columns_names = " ".join([column_name[1] for column_name in db['column_names_original'] ])
            tables_with_columns = ''
            for table_id, group in itertools.groupby(db['column_names_original'], lambda x: x[0]):
              if table_id == -1:
                continue

              columns_names = " ".join([column_name[1] for column_name in group ])
              tables_with_columns += '<t> ' + db_tables[table_id] + ' <c> ' + columns_names + ' </c> ' + '</t> '


            # group columns with tables. 

            db_with_question = 'translate English to SQL: ' + element['question'] + ' ' + tables_with_columns + '</s>'
            # question_with_schema = 'translate English to GraphQL: ' + element['question']  + ' ' + ' '.join(self.name_to_schema[element['schemaId']]) + ' </s>'

            tokenized_s = tokenizer.batch_encode_plus([db_with_question],max_length=1024, pad_to_max_length=True, truncation=True,return_tensors='pt')
            # what is the largest example size?
            # the alternative is to collate
            #might need to collate
            self.source.append(tokenized_s)

            tokenized_t = tokenizer.batch_encode_plus([element['query'] + ' </s>'],max_length=block_size, pad_to_max_length=True, truncation=True,return_tensors='pt')
            self.target.append(tokenized_t)


  def __len__(self):
        'Denotes the total number of samples'
        return len(self.source)

  def __getitem__(self, index):
        'Generates one sample of data'
        source_ids = self.source[index]['input_ids'].squeeze()
        target_ids = self.target[index]['input_ids'].squeeze()
        src_mask = self.source[index]['attention_mask'].squeeze()
        return { 'source_ids': source_ids,
                'source_mask': src_mask,
                'target_ids': target_ids,
                'target_ids_y': target_ids}

In [13]:
tokenizer = AutoTokenizer.from_pretrained("t5-base")
dataset = SpiderDataset(tokenizer=tokenizer , type_path='train_spider.json', block_size=102)

length = dataset.__len__()
item = dataset.__getitem__(0)

/Users/jakobtolstrup/opt/anaconda3/lib/python3.9/site-packages/transformers/tokenization_utils_base.py:2226: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


In [14]:
class CoSQLMaskDataset(Dataset):
  'Characterizes a dataset for PyTorch'
  def __init__(self, tokenizer, type_path='cosql_train.json', block_size=64):
        'Initialization'
        super(CoSQLMaskDataset, ).__init__()
        self.tokenizer = tokenizer

        self.source = []
        self.target = []
        path = './cosql_dataset/sql_state_tracking/' + type_path
        with open(path, 'r') as f:
          data = json.load(f)
          for element in data:
            for interaction in element['interaction']:
              # repeat the squence for the amount of tokens. 
              # loop through those sequences and replace a different token in each one. 
              # the target will be that token. 
              utterance = interaction['query']
              # tokens = utterance.split()
              encoded_source = tokenizer.encode(utterance, max_length=block_size, pad_to_max_length=True, truncation=True, return_tensors='pt').squeeze()
              token_count = encoded_source.shape[0]
              # print(encoded_source.shape)
              repeated_utterance = [encoded_source for _ in range(token_count)]
              for pos in range(1, token_count):
                encoded_source = repeated_utterance[pos].clone()
                target_id = encoded_source[pos].item()
                if target_id == tokenizer.eos_token_id:
                  break
                # encoded_source[pos] = tokenizer.mask_token_id
                # self.target.append(target_id)
                # self.source.append(encoded_source)

                encoded_source[pos] = tokenizer.mask_token_id
                decoded_target = ''.join(tokenizer.convert_ids_to_tokens([target_id])) + ' </s>'
                encoded_target = tokenizer.encode(decoded_target, return_tensors='pt', max_length=4, pad_to_max_length=True, truncation=True).squeeze() # should always be of size 1
                self.target.append(encoded_target)
                self.source.append(encoded_source)

                # repeated_utterance[pos][pos] = target_token # so that the next iteration the previous token is correct

                
          

  def __len__(self):
        'Denotes the total number of samples'
        return len(self.source)

  def __getitem__(self, index):
        'Generates one sample of data'
        source_ids = self.source[index]#['input_ids'].squeeze()
        target_id = self.target[index]#['input_ids'].squeeze()
        # src_mask = self.source[index]['attention_mask'].squeeze()
        return { 'source_ids': source_ids,
                'target_id': target_id}
                # 'source_mask': src_mask,
                # 'target_ids': target_ids,
                # 'target_ids_y': target_ids}

In [15]:
# tokenizer = AutoTokenizer.from_pretrained("t5-base")

# special_tokens_dict = tokenizer.special_tokens_map # the issue could be here, might need to copy.
# special_tokens_dict['mask_token'] = '<mask>'
# special_tokens_dict['additional_special_tokens'] = ['<t>', '</t>', '<a>', '</a>']
# tokenizer.add_tokens(['{', '}', '<c>', '</c>'])
# tokenizer.add_special_tokens(special_tokens_dict)
# #model.resize_token_embeddings(len(tokenizer))
# print(tokenizer.mask_token)

# dataset = CoSQLMaskDataset(tokenizer=tokenizer , type_path='cosql_train.json', block_size=64)

# length = dataset.__len__()
# item = dataset.__getitem__(0)

# Model

In [16]:
class T5MultiSPModel(pl.LightningModule):
  def __init__(self, hyperparams, task='denoise', test_flag='graphql', train_sampler=None, batch_size=2,temperature=1.0,top_k=50, top_p=1.0, num_beams=1 ):
    super(T5MultiSPModel, self).__init__()

    self.temperature = temperature
    self.top_k = top_k
    self.top_p = top_p
    self.num_beams = num_beams

    self.hyperparams = hyperparams

    self.task = task
    self.test_flag = test_flag
    self.train_sampler = train_sampler
    self.batch_size = batch_size
    if self.task == 'finetune':
      self.model = T5ForConditionalGeneration.from_pretrained('t5-base')
    else: 
      self.model = T5ForConditionalGeneration.from_pretrained('t5-base') # no output past? 

    self.tokenizer = T5Tokenizer.from_pretrained('t5-base')
    
    self.criterion = torch.nn.CrossEntropyLoss(ignore_index=self.tokenizer.pad_token_id)
    self.add_special_tokens()

  def forward(
    self, input_ids, attention_mask=None, decoder_input_ids=None, decoder_attention_mask=None, labels=None
    ):
    return self.model(
        input_ids,
        attention_mask=attention_mask,
        decoder_input_ids=decoder_input_ids,
        decoder_attention_mask=decoder_attention_mask,
        labels=labels,
    )

  def add_special_tokens(self):
    # new special tokens
    special_tokens_dict = self.tokenizer.special_tokens_map # the issue could be here, might need to copy.
    special_tokens_dict['mask_token'] = '<mask>'
    special_tokens_dict['additional_special_tokens'] = ['<t>', '</t>', '<a>', '</a>']
    self.tokenizer.add_tokens(['{', '}', '<c>', '</c>'])
    self.tokenizer.add_special_tokens(special_tokens_dict)
    self.model.resize_token_embeddings(len(self.tokenizer))

  def _step(self, batch):
    if self.task == 'finetune':
      pad_token_id = self.tokenizer.pad_token_id
      source_ids, source_mask, y = batch["source_ids"], batch["source_mask"], batch["target_ids"]
      # y_ids = y[:, :-1].contiguous()
      labels = y[:, :].clone()
      labels[y[:, :] == pad_token_id] = -100
      # attention_mask is for ignore padding on source_ids 
      # labels need to have pad_token ignored manually by setting to -100
      # todo check the ignore token for forward
      # seems like decoder_input_ids can be removed. 
      outputs = self(source_ids, attention_mask=source_mask, labels=labels,)

      loss = outputs[0]

    else: 
      y = batch['target_id']
      labels = y[:, :].clone()
      labels[y[:, :] == self.tokenizer.pad_token_id] = -100
      loss = self(
          input_ids=batch["source_ids"],
          labels=labels
      )[0]


    return loss

  def training_step(self, batch, batch_idx):
    loss = self._step(batch)

    tensorboard_logs = {"train_loss": loss}
    return {"loss": loss, "log": tensorboard_logs}

  def validation_step(self, batch, batch_idx):
    loss = self._step(batch)
      
    # if self.task == 'finetune':
    #   preds, target = self._generate_step(batch)
    #   accuracy = exact_match.exact_match_accuracy(preds,target)
    #   return {"val_loss": loss, "val_acc": torch.tensor(accuracy) }
    # else:
    return {"val_loss": loss}

  def validation_epoch_end(self, outputs):
    avg_loss = torch.stack([x["val_loss"] for x in outputs]).mean()
    # if self.task == 'finetune':
    #   avg_acc = torch.stack([x["val_acc"] for x in outputs]).mean()
    #   tensorboard_logs = {"val_loss": avg_loss, "avg_val_acc": avg_acc}
    #   return {"progress_bar": tensorboard_logs, "log": tensorboard_logs}
    # else:
    tensorboard_logs = {"val_loss": avg_loss}
    return {'progress_bar': tensorboard_logs, 'log': tensorboard_logs }
    

  # def optimizer_step(self, epoch, batch_idx, optimizer, optimizer_idx, second_order_closure=None):
  #   if self.trainer:
  #     xm.optimizer_step(optimizer)
  #   else:
  #     optimizer.step()
  #   optimizer.zero_grad()
  #   self.lr_scheduler.step()


  def configure_optimizers(self):
    t_total = len(self.train_dataloader()) * self.trainer.max_epochs * self.trainer.limit_train_batches
    no_decay = ["bias", "LayerNorm.weight"]
    optimizer_grouped_parameters = [
        {
            "params": [p for n, p in self.named_parameters() if not any(nd in n for nd in no_decay)],
            "weight_decay": 0.0,
        },
        {"params": [p for n, p in self.named_parameters() if any(nd in n for nd in no_decay)], "weight_decay": 0.0},
    ]
    optimizer = AdamW(optimizer_grouped_parameters, lr=self.hyperparams.lr, eps=1e-8)
    scheduler = get_linear_schedule_with_warmup(
        optimizer, num_warmup_steps=0, num_training_steps=t_total
    )
    self.lr_scheduler = scheduler
    return [optimizer] #, [scheduler]

  def _generate_step(self, batch):
    generated_ids = self.model.generate(
        batch["source_ids"],
        attention_mask=batch["source_mask"],
        num_beams=self.num_beams,
        max_length=1000,
        temperature=self.temperature,
        top_k=self.top_k,
        top_p=self.top_p,
        length_penalty=1.0,
        early_stopping=True,
    )

    preds = [
        self.tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=True)
        for g in generated_ids
    ]
    target = [
        self.tokenizer.decode(t, skip_special_tokens=True, clean_up_tokenization_spaces=True)
        for t in batch["target_ids"]
    ]
    return (preds, target)

  def test_step(self, batch, batch_idx):
    preds, target = self._generate_step(batch)
    loss = self._step(batch)
    if self.test_flag == 'graphql':
      accuracy = exact_match.exact_match_accuracy(preds,target)
      return {"test_loss": loss, "test_accuracy": torch.tensor(accuracy)}
    else: 
      return {"test_loss": loss, "preds": preds, "target": target }

  # def test_end(self, outputs):
  #   return self.validation_end(outputs)


  def test_epoch_end(self, outputs):
    avg_loss = torch.stack([x["test_loss"] for x in outputs]).mean()
    
    if self.test_flag == 'graphql':
      avg_acc = torch.stack([x["test_accuracy"] for x in outputs]).mean()
      tensorboard_logs = {"test_loss": avg_loss, "test_acc": avg_acc}
      return {"progress_bar": tensorboard_logs, "log": tensorboard_logs}

    else:
      output_test_predictions_file = os.path.join(os.getcwd(), "test_predictions.txt")
      with open(output_test_predictions_file, "w+") as p_writer:
          for output_batch in outputs:
              p_writer.writelines(s + "\n" for s in output_batch["preds"])
          p_writer.close()
      tensorboard_logs = {"test_loss": avg_loss}
      return {"progress_bar": tensorboard_logs, "log": tensorboard_logs}

  def prepare_data(self):
    if self.task == 'finetune':
      self.train_dataset_g = TextToGraphQLDataset(self.tokenizer)
      self.val_dataset_g = TextToGraphQLDataset(self.tokenizer, type_path='dev.json')
      self.test_dataset_g = TextToGraphQLDataset(self.tokenizer, type_path='dev.json')

      self.train_dataset_s = SpiderDataset(self.tokenizer)
      self.val_dataset_s = SpiderDataset(self.tokenizer, type_path='dev.json')
      self.test_dataset_s = SpiderDataset(self.tokenizer, type_path='dev.json')

      self.train_dataset = ConcatDataset([self.train_dataset_g,self.train_dataset_s])
      self.val_dataset = ConcatDataset([self.val_dataset_g, self.val_dataset_s])
      # self.test_dataset = ConcatDataset([test_dataset_g, test_dataset_s])
      if self.test_flag == 'graphql':
        self.test_dataset = self.test_dataset_g
      else:
        self.test_dataset = self.test_dataset_s
      
    else:
      train_dataset_g = MaskGraphQLDataset(self.tokenizer)
      val_dataset_g = MaskGraphQLDataset(self.tokenizer, type_path='dev.json')

      train_dataset_s = CoSQLMaskDataset(self.tokenizer)
      val_dataset_s = CoSQLMaskDataset(self.tokenizer, type_path='cosql_dev.json')

      self.train_dataset = ConcatDataset([train_dataset_g, train_dataset_s])
      self.val_dataset = ConcatDataset([val_dataset_g,val_dataset_s])

  def train_dataloader(self):
    return DataLoader(self.train_dataset, batch_size=self.batch_size, shuffle=True)

  def val_dataloader(self):
    return DataLoader(self.val_dataset, batch_size=self.batch_size)

  def test_dataloader(self):
    return DataLoader(self.test_dataset, batch_size=self.batch_size)



In [17]:
# %load_ext tensorboard
%reload_ext tensorboard

%tensorboard --logdir lightning_logs/


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


# Pre-training

In [18]:
# tokenizer = BartTokenizer.from_pretrained('bart-large')
# dataset = ConvDataset(tokenizer)

In [19]:
import argparse

In [20]:
hyperparams = argparse.Namespace(**{'lr': 0.0004365158322401656}) # for 3 epochs

In [21]:
# system = ConvBartSystem(dataset, train_sampler, batch_size=2)
system = T5MultiSPModel(hyperparams,batch_size=32)
# system.lr = 3e-4

In [22]:
from pytorch_lightning.callbacks import ModelCheckpoint
# trainer = Trainer(num_tpu_cores=8,max_epochs=1)   
# trainer = Trainer(max_epochs=1, limit_train_batches=0.1)
# checkpoint_callback = ModelCheckpoint(
#     filepath=os.getcwd()+'/checkpoint',
#     verbose=True,
#     monitor='val_loss',
#     mode='min',
#     prefix=''
# )
# trainer = Trainer(gpus=1, max_epochs=1, progress_bar_refresh_rate=1)
#trainer = Trainer(gpus=1, max_epochs=1, progress_bar_refresh_rate=1, limit_train_batches=0.2)
trainer = Trainer(accelerator='cpu', max_epochs=1, log_every_n_steps=1, limit_train_batches=0.2)
# trainer = Trainer(gpus=1, max_epochs=3, auto_lr_find=True, progress_bar_refresh_rate=1, limit_train_batches=0.2)\
# trainer = Trainer(gpus=1,max_epochs=1, progress_bar_refresh_rate=1, limit_train_batches=0.2)
# trainer = Trainer(gpus=1,max_epochs=1, progress_bar_refresh_rate=1, limit_train_batches=0.2,checkpoint_callback=checkpoint_callback)
# trainer = Trainer(num_tpu_cores=8,max_epochs=1, progress_bar_refresh_rate=1)

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


In [23]:
# Print the version of PyTorch Lightning
print(pl.__version__)

1.9.3


In [24]:
# import gc
# gc.collect()

trainer.fit(system)

/Users/jakobtolstrup/opt/anaconda3/lib/python3.9/site-packages/transformers/models/t5/tokenization_t5.py:191: UserWarning: This sequence already has </s>. In future versions this behavior may lead to duplicated eos tokens being added.
  warnings.warn(
/Users/jakobtolstrup/opt/anaconda3/lib/python3.9/site-packages/transformers/tokenization_utils_base.py:2226: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(

  | Name      | Type                       | Params
---------------------------------------------------------
0 | model     | T5ForConditionalGeneration | 222 M 
1 | criterion | CrossEntropyLoss  

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Sanity Checking: 0it [00:00, ?it/s]

/Users/jakobtolstrup/opt/anaconda3/lib/python3.9/site-packages/pytorch_lightning/trainer/connectors/data_connector.py:224: PossibleUserWarning: The dataloader, val_dataloader 0, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 8 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  rank_zero_warn(
/Users/jakobtolstrup/opt/anaconda3/lib/python3.9/site-packages/pytorch_lightning/trainer/connectors/data_connector.py:224: PossibleUserWarning: The dataloader, train_dataloader, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 8 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  rank_zero_warn(


Training: 0it [00:00, ?it/s]

/Users/jakobtolstrup/opt/anaconda3/lib/python3.9/site-packages/pytorch_lightning/trainer/call.py:48: UserWarning: Detected KeyboardInterrupt, attempting graceful shutdown...
  rank_zero_warn("Detected KeyboardInterrupt, attempting graceful shutdown...")


Running the next two blocks probably uses memory unless I use without gradient.


In [ ]:
# system.tokenizer.decode(system.train_dataset[0]['source_ids'].squeeze(), skip_special_tokens=False, clean_up_tokenization_spaces=False)

'query <mask> faculty_aggregate { aggregate { count } } } '

In [ ]:
# TXT = "query { faculty_aggregate { aggregate { <mask> } } } </s>"
# input_ids = system.tokenizer.batch_encode_plus([TXT], return_tensors='pt')['input_ids']

# logits = system.model(input_ids)[0]

In [ ]:
#system.tokenizer.decode(system.model.generate(input_ids.cuda())[0])

'count'

# Finetune

In [ ]:
# len(system.val_dataloader().dataset)

In [ ]:
# system = TextGraphQLModel.load_from_checkpoint('./_ckpt_epoch_0_v0.ckpt' )

In [ ]:
#system.hyperparams

Namespace(lr=0.0004365158322401656)

In [ ]:
# system.task = 'finetune'
# system.batch_size = 2 # because t5-base is smaller than bart.
# # system.lr=3e-4 # -6 is original
# # system.batch_size = 16
# system.hyperparams.lr=0.0005248074602497723 # same as 5e-4
# # system.hyperparams.lr=3e-4
# # TODO collate to go back to 16
# # system.model.config.output_past=True
# # system.model.model.decoder.output_past=True
# system.prepare_data() # might not be needed. 
# # system.add_special_tokens()
# # system.model.output_past = True

shouldn't we monitor: `avg_val_loss`?

In [ ]:
# from pytorch_lightning.callbacks import ModelCheckpoint
# # trainer = Trainer(num_tpu_cores=8,max_epochs=1)   
# # trainer = Trainer(max_epochs=1, limit_train_batches=0.1)
# # checkpoint_callback = ModelCheckpoint(
# #     filepath=os.getcwd()+'/checkpoint_finetuning',
# #     verbose=True,
# #     monitor='val_loss',
# #     mode='min',
# #     prefix=''
# # )

# # trainer = Trainer(gpus=1,max_epochs=1, progress_bar_refresh_rate=1, limit_train_batches=0.2)
# # trainer = Trainer(gpus=1, progress_bar_refresh_rate=1, val_check_interval=0.4)
# trainer = Trainer(gpus=1, max_epochs=5, progress_bar_refresh_rate=1, val_check_interval=0.5)
# # trainer = Trainer(gpus=1, max_epochs=3, progress_bar_refresh_rate=1, val_check_interval=0.5)
# # trainer = Trainer(gpus=1,max_epochs=3, progress_bar_refresh_rate=1,checkpoint_callback=checkpoint_callback)
# # trainer = Trainer(num_tpu_cores=8,max_epochs=1, progress_bar_refresh_rate=1)

GPU available: True, used: True
No environment variable for node rank defined. Set as 0.
CUDA_VISIBLE_DEVICES: [0]


In [ ]:
# trainer.fit(system)


    | Name                                                                  | Type                       | Params
-----------------------------------------------------------------------------------------------------------------
0   | model                                                                 | T5ForConditionalGeneration | 222 M 
1   | model.shared                                                          | Embedding                  | 24 M  
2   | model.encoder                                                         | T5Stack                    | 109 M 
3   | model.encoder.block                                                   | ModuleList                 | 84 M  
4   | model.encoder.block.0                                                 | T5Block                    | 7 M   
5   | model.encoder.block.0.layer                                           | ModuleList                 | 7 M   
6   | model.encoder.block.0.layer.0                                         | T5LayerSe

/usr/local/lib/python3.6/dist-packages/pytorch_lightning/utilities/distributed.py:23: UserWarning: The dataloader, train dataloader, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` in the `DataLoader` init to improve performance.
  warnings.warn(*args, **kwargs)


1

In [ ]:
# inputs = system.val_dataset[0]
# system.tokenizer.decode(inputs['source_ids'])

# # system.tokenizer.decode(inputs['target_ids'])

"translate English to GraphQL: How many ships ended up being 'Captured'? <t> battle { bulgarian_commander date id latin_commander name result ships ships_aggregate } </t> <t> battle_aggregate { aggregate nodes } </t> <t> death { caused_by_ship_id id injured killed note ship } </t> <t> death_aggregate { aggregate nodes } </t> <t> ship { battle deaths deaths_aggregate disposition_of_ship id location lost_in_battle name ship_type tonnage } </t> <t> ship_aggregate { aggregate nodes } </t> <a> distinct_on limit offset order_by where </a> "

In [ ]:
# # inputs = system.tokenizer.batch_encode_plus([user_input], max_length=1024, return_tensors='pt')
# # generated_ids = system.bart.generate(example['input_ids'].cuda(), attention_mask=example['attention_mask'].cuda(), num_beams=5, max_length=40,repetition_penalty=3.0)
# # maybe i didn't need attention_mask? or the padding was breaking something.
# # attention mask is only needed  
# generated_ids = system.model.generate(inputs['source_ids'].unsqueeze(0).cuda(), num_beams=5, repetition_penalty=1.0, max_length=56, early_stopping=True)
# # summary_text = system.tokenizer.decode(generated_ids[0])

# hyps = [system.tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=False) for g in generated_ids]

In [ ]:
# print(hyps)

['query { ship_aggregate ( where : { name : { _eq : "Captured" } } ) { aggregate { count } } }']


improving the network: 
- can it handle <, > ? any other missing could check the dataset directy for unk
- try to increase the learning rate an order of magnitude.

In [ ]:
# trainer.save_checkpoint('finished.ckpt')

In [ ]:
# !zip -r finished_train.zip finished.ckpt

  adding: finished.ckpt (deflated 7%)


The cells below is used to load a checkpoint instead of training.

In [ ]:
# from google.colab import drive
# drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [ ]:
# from google.colab import drive
# drive.flush_and_unmount()

In [ ]:
# !cp ./drive/My\ Drive/ssh_files/finished_train.zip ./finished_train.zip

In [ ]:
# !unzip ./finished_train.zip

Archive:  ./finished_train.zip
  inflating: finished.ckpt           


In [ ]:
# system = system.load_from_checkpoint('finished.ckpt')
# system.task='finetune'
# trainer = Trainer(gpus=1, max_epochs=0, progress_bar_refresh_rate=1, val_check_interval=0.5)
# trainer.fit(system)


Some weights of T5ForConditionalGeneration were not initialized from the model checkpoint at t5-base and are newly initialized: ['encoder.embed_tokens.weight', 'decoder.embed_tokens.weight', 'lm_head.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
CUDA_VISIBLE_DEVICES: [0]

  | Name      | Type                       | Params
---------------------------------------------------------
0 | model     | T5ForConditionalGeneration | 222 M 
1 | criterion | CrossEntropyLoss           | 0     
/usr/local/lib/python3.6/dist-packages/pytorch_lightning/utilities/distributed.py:25: UserWarning: The dataloader, val dataloader 0, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 2 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  warnings.warn(*

/usr/local/lib/python3.6/dist-packages/pytorch_lightning/utilities/distributed.py:25: UserWarning: The dataloader, train dataloader, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 2 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  warnings.warn(*args, **kwargs)


1

# Test

In [ ]:
# system.num_beams = 3
# system.test_flag = 'graphql'
# system.prepare_data()
# trainer.test()

/usr/local/lib/python3.6/dist-packages/pytorch_lightning/utilities/distributed.py:23: UserWarning: The dataloader, test dataloader 0, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` in the `DataLoader` init to improve performance.
  warnings.warn(*args, **kwargs)


--------------------------------------------------------------------------------
TEST RESULTS
{'test_acc': tensor(0.5018), 'test_loss': tensor(0.2084, device='cuda:0')}
--------------------------------------------------------------------------------



In [ ]:
# system.num_beams = 3
# system.test_flag = 'sql'
# system.prepare_data()
# trainer.test()

--------------------------------------------------------------------------------
TEST RESULTS
{'test_loss': tensor(0.2084, device='cuda:0')}
--------------------------------------------------------------------------------



In [ ]:
# import nltk
# nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [ ]:
# !cd spider && git clone https://github.com/taoyds/spider

fatal: destination path 'spider' already exists and is not an empty directory.


In [ ]:
# !cd spider && python ./spider/evaluation.py --gold dev_gold.sql --pred ../test_predictions.txt --etype match --db ./database --table tables.json



easy pred: SELECT count(*) FROM singer GROUP BY singer_id ORDER BY count(*) DESC LIMIT 1; order_by : { song_name ASC LIMIT 1; order_by : { song_name ASC LIMIT 1; order_by : { vocalist_id DESC LIMIT 1; order_by : { song_name ASC LIMIT 1; order_by : { song_name ASC LIMIT 1; order_by : {
easy gold: SELECT count(*) FROM singer

easy pred: SELECT count(*) FROM singer GROUP BY singer_id ORDER BY count(*) DESC LIMIT 1; order_by : { song_name ASC LIMIT 1; order_by : { song_name ASC LIMIT 1; order_by : { vocalist_id DESC LIMIT 1; order_by : { song_name ASC LIMIT 1; order_by : { count(*) DESC LIMIT 1; order_by
easy gold: SELECT count(*) FROM singer

medium pred: SELECT name, country, age FROM singer ORDER BY age DESC LIMIT 1; ORDER BY age DESC LIMIT 1; ORDER BY age DESC LIMIT 1; order_by : { age DESC LIMIT 1; order_by : { age DESC LIMIT 1; order_by : { age DESC LIMIT 1; order_by : { age DESC LIMIT 1; order_by : { age DESC LIMIT 1; order_by : { age DESC LIMIT 1; order_by : asc } age DESC LIMIT 1;

# Inference server

In [ ]:
# !pip install flask-ngrok

In [ ]:
# pip install -U flask-cors

In [ ]:
# from flask_ngrok import run_with_ngrok
# from flask import Flask, jsonify, request, make_response
# from flask_cors import CORS
# app = Flask(__name__)
# CORS(app)
# run_with_ngrok(app)   #starts ngrok when the app is run

# @app.route('/', methods=['GET', 'POST'])
# @app.route("/predict", methods=['GET', 'POST'])
# def predict():
#   # if request.method == 'POST':
#     # req_content = request.get_json()
#     # print("request ", req_content)
#   req_json = request.get_json()
#   print(request)
#   print(req_json)
#   prompt = req_json['prompt']
#   schemaId = req_json['schemaId']
#   if system.train_dataset_g.name_to_schema[schemaId] is not None:
#     input_string = system.train_dataset_g.get_question_with_schema(prompt, schemaId)
#   elif system.dev_dataset.name_to_schema[schemaId] is not None:
#     input_string = system.val_dataset_g.get_question_with_schema(prompt, schemaId)
#   print(input_string)
  
#   # val_inputs = system.val_dataset[0]
#   # print(system.tokenizer.decode(val_inputs['source_ids'], skip_special_tokens=False))

#   inputs = system.tokenizer.batch_encode_plus([input_string], max_length=1024, return_tensors='pt')['input_ids']

#   print(inputs.shape)
#   # print(val_inputs['source_ids'].shape)


#   # generated_ids = system.model.generate(val_inputs['source_ids'].unsqueeze(0).cuda(), num_beams=1, repetition_penalty=1.0, max_length=1000, early_stopping=True)
#   generated_ids = system.model.generate(inputs.cuda(), num_beams=3, repetition_penalty=1.0, max_length=1000, early_stopping=True)
#   hyps = [system.tokenizer.decode(g, skip_special_tokens=True, clean_up_tokenization_spaces=False) for g in generated_ids]
#   print(hyps)
#   dict_res = { "prediction" : hyps[0]}
#   print(dict_res)
#   return jsonify(dict_res)


# app.run()

 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://127.0.0.1:5000/ (Press CTRL+C to quit)


 * Running on http://9a8c140c591b.ngrok.io
 * Traffic stats available on http://127.0.0.1:4040


127.0.0.1 - - [29/Jun/2020 21:36:27] "OPTIONS / HTTP/1.1" 200 -
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'only_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you may want to check this is the right behavior.


<Request 'http://9a8c140c591b.ngrok.io/' [POST]>
{'prompt': 'Find the name of the employee who got the highest one time bonus.', 'schemaId': 'employee_hire_evaluation'}
translate English to GraphQL: Find the name of the employee who got the highest one time bonus. <t> employee { age city employee_id evaluations evaluations_aggregate hirings hirings_aggregate name } </t> <t> employee_aggregate { aggregate nodes } </t> <t> evaluation { bonus employee employee_id year_awarded } </t> <t> evaluation_aggregate { aggregate nodes } </t> <t> hiring { employee employee_id is_full_time shop shop_id start_from } </t> <t> hiring_aggregate { aggregate nodes } </t> <t> shop { district hirings hirings_aggregate location manager_name name number_products shop_id } </t> <t> shop_aggregate { aggregate nodes } </t> <a> distinct_on limit offset order_by where </a> </s>
torch.Size([1, 169])


...

['query { airlines ( where : { abbreviation : { _eq : "UAL" } } ) { airline } }']
{'prediction': 'query { airlines ( where : { abbreviation : { _eq : "UAL" } } ) { airline } }'}


127.0.0.1 - - [29/Jun/2020 21:43:37] "OPTIONS / HTTP/1.1" 200 -
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'only_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you may want to check this is the right behavior.


<Request 'http://9a8c140c591b.ngrok.io/' [POST]>
{'prompt': "Give the airline with abbreviation 'UAL'.", 'schemaId': 'flight_2'}
translate English to GraphQL: Give the airline with abbreviation 'UAL'. <t> airlines { abbreviation airline country flights flights_aggregate uid } </t> <t> airlines_aggregate { aggregate nodes } </t> <t> airports { airportcode airportname city country countryabbrev flightsByDestairport flightsByDestairport_aggregate flightsBySourceairport flightsBySourceairport_aggregate } </t> <t> airports_aggregate { aggregate nodes } </t> <t> flights { airline airlineByAirline airportByDestairpot airportBySourceairport destairport flightno sourceairport } </t> <t> flights_aggregate { aggregate nodes } </t> <a> distinct_on limit offset order_by where </a> </s>
torch.Size([1, 165])


127.0.0.1 - - [29/Jun/2020 21:43:38] "POST / HTTP/1.1" 200 -


['query { airlines ( where : { abbreviation : { _eq : "UAL" } } ) { airline } }']
{'prediction': 'query { airlines ( where : { abbreviation : { _eq : "UAL" } } ) { airline } }'}
